# Embeddings

A ideia por de trás de Word Embeddings é que é possível representar uma palavra usando um vetor compacto e denso que preserve sua conotação, ou seja, seu **significado inferido a partir de um contexto**.

A técnica que deu início aos Words Embeddings foi divulgada num paper de 2013, do Google. Essa técnica recebeu o nome de Word2Vec e vamos entender seu funcionamento agora.

## Word2Vec

O que significa dizer que uma representação textual deveria capturar a similaridade distribucional entre palavras? Vamos analisar alguns exemplos. Se eu fornecer a palavra “Brasil”, outras palavras com similaridade distribucional a essa poderiam ser outros países (“Chile”, “Uruguai”, etc.). Se eu forneço a palavra “Bela”, poderia pensar em sinônimos ou antônimos como palavras com similaridade distribucional. Ou seja, o que estamos tentando capturar são palavras que possuem alta probabilidade de aparecerem num mesmo contexto.

Ao aprender tais relações semânticas, o Word2Vec garante que a representação aprendida possui baixa dimensionalidade (palavras são representadas por vetores de 50-1000 dimensões) e são densas (a maioria dos valores dos vetores são diferentes de zero). Tais representações tornam as tarefas de modelos de machine learning mais eficientes.

Antes de entrarmos nos detalhes de como o Word2Vec consegue capturar tais relações, vamos construir uma intuição de como ele funciona. Dado um corpus de texto, o objetivo é aprender embeddings de cada palavra no corpus de modo que o vetor da palavra no espaço de embeddings melhor captura o significado da palavra. Para isso, Word2Vec usa similaridade distribucional e hipótese distribucional, ou seja, extrai o significado de uma palavra a partir do seu contexto. Assim, se duas palavras geralmente ocorrem em contextos similares, é altamente provável que seus significados sejam também similares.

Dessa maneira, o Word2Vec projeta o significado das palavras num espaço vetorial onde palavras com significados similares tendem a serem agrupadas juntas e palavras com significados muito diferentes estão longe umas das outras.

Conceitualmente, o que queremos saber é, dada uma palavra e as palavras que aparecem em seu contexto , como encontramos um vetor que melhor representa o significado da palavra? Bom, para cada palavra no corpus, iniciamos um vetor com valores aleatórios. O modelo Word2Vec refina os valores predizendo dados os vetores de palavras no contexto . Isto é feito através de uma rede neural de duas camadas, mas antes de construir a rede neural de duas camadas, vamos ver modelos pré-treinados.

## Prática

A primeira coisa a ser feita é importar os pacotes necessários:

In [1]:
import numpy as np
import pandas as pd
import gensim
from gensim.models import Word2Vec
import re
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import random
import time
import string
import unicodedata
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
from sklearn import svm
from sklearn import metrics
import multiprocessing

Depois, vamos ler o mesmo arquivo que usamos anteriormente, para fazermos uma comparação com os tipos de representação vistos nas aulas passadas.

In [2]:
df = pd.read_csv("https://dados-ml-pln.s3-sa-east-1.amazonaws.com/produtos.csv", delimiter=";", encoding='utf-8')
df.dropna(inplace=True)
df["texto"] = df['nome'] + " " + df['descricao']
df = df.loc[:, ['categoria', 'texto']]
df.head(3)

categoria                                              texto
0     livro   O Hobbit - 7ª Ed. 2013  Produto NovoBilbo Bol...
1     livro   Livro - It A Coisa - Stephen King  Produto No...
2     livro   Box  As Crônicas De Gelo E Fogo  Pocket  5 Li...

In [3]:
df.shape

(2916, 2)

In [4]:
df.head(20)

categoria                                              texto
0      livro   O Hobbit - 7ª Ed. 2013  Produto NovoBilbo Bol...
1      livro   Livro - It A Coisa - Stephen King  Produto No...
2      livro   Box  As Crônicas De Gelo E Fogo  Pocket  5 Li...
3      livro   Box Harry Potter  Produto Novo e Físico  A sé...
4      livro   Livro Origem - Dan Brown  Produto NovoDe Onde...
5      livro   Mais Escuro - Cinquenta Tons Mais Escuros Pel...
6      livro   O Silmarillion - 5ª Ed. 2011  Produto NovoO S...
7      livro   O Pequeno Principe  O Pequeno Príncipe é um d...
8      livro   Ed & Lorraine Warren - Demonologistas  Arquiv...
9      livro   Box - Franz Kafka 1883-1924 - 3 Livros  Produ...
10     livro   Livros The Walking Dead-envio Imediato- Promo...
12     livro   It - A Coisa  Produto Novo e Físico  Durante ...
13     livro   Bibliocanto Organizador Separador De Livros  ...
14     livro   Gravity Falls Journal 3  Produto Novo e Físic...
15     livro   Nutri Ninja Auto Iq + Livro 220v  Sabe-se que...
16     livro   Outros Jeitos De Usar A Boca  Produto NovoOut...
17     livro   Caixa De Pássaros  Produto NovoRomance de est...
18     livro   Extraordinario  Produto Novo e Físico  August...
19     livro   Box - Irmãos Maddox - 5 Livros  Edição Econôm...
20     livro   Uma Pergunta Por Dia  Produto NovoTodos os di...

Agora, precisamos embaralhar os dados. Com isso, evitamos que o modelo aprenda bem somente sobre uma classe, já que ele pode ficar preso em mínimos locais. Para isso, usaremos o método Shuffle, da biblioteca utils da Scikit-Learn. Por fim, reiniciamos o index e eliminamos a nova coluna de índice criada e mostramos as 5 primeiras linhas de nosso dataset.

In [6]:
df = shuffle(df)
df = df.reset_index(drop=True)
df.head(10)

categoria                                              texto
0      livro   O Apanhador No Campo De Centeio  Produto Novo...
1  brinquedo   Boneco One Piece Styling Law Luffy Zoro Mihaw...
2      livro   Box Série Fallen 5 Livros Lauren Kate  Box Sé...
3       game   Mini Game Portátil 10mil Jogos Player Mp3 Mp4...
4  maquiagem   Kit Anel Micropigmentação 2 Anéis + 100 Batoq...
5  maquiagem   1 Um Par De Cílios Postiços Crème Shop 100% C...
6       game   (promo)3100 Gold Wow Ouro Horda Azralon  Cons...
7      livro   Deuses Americanos  Produto NovoObra-prima de ...
8  maquiagem   Paleta Corretivo Contorno Ruby Rose 12 Cores ...
9      livro   Coleção: Game Of Thrones 6 Livros - Cronicas ...

In [7]:
set(df['categoria'])

{'brinquedo', 'game', 'livro', 'maquiagem'}

In [8]:
df['categoria'].value_counts()

categoria
livro        838
maquiagem    788
brinquedo    668
game         622
Name: count, dtype: int64

Vamos usar o mesmo conjunto de funções para tratamento de texto que escrevemos. Vou colocá-lo aqui e relembrar brevemente o que cada função faz:

In [9]:
nltk.download('stopwords')
nltk.download('punkt')

def normalize_accents(text):
    return unicodedata.normalize("NFKD", text).encode("ASCII", "ignore").decode("utf-8")

def normalize_str(text):
    text = text.lower()
    text = remove_punctuation(text)
    text = normalize_accents(text)
    text = re.sub(re.compile(r" +"), " ",text)
    return " ".join([w for w in text.split()])

def remove_punctuation(text):
    punctuations = string.punctuation
    table = str.maketrans({key: " " for key in punctuations})
    text = text.translate(table)
    return text


def tokenizer(text):
    stop_words = nltk.corpus.stopwords.words("portuguese") # portuguese, caso o dataset seja em português
    if isinstance(text, str):
        text = normalize_str(text)
        text = "".join([w for w in text if not w.isdigit()])
        text = word_tokenize(text)
        text = [x for x in text if x not in stop_words]
        text = [y for y in text if len(y) > 2]
        return [t for t in text] #lista de palavras
    else:
        return None

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


Novamente, aplicamos essas funções para tratar o texto de todas as linhas da coluna Title. O texto tratado estará dentro da nova coluna criada chamada Title_treated.

In [10]:
df['texto_Treated'] = df['texto'].apply(tokenizer)

In [11]:
df.head() # verificando os resultados

categoria                                              texto  \
0      livro   O Apanhador No Campo De Centeio  Produto Novo...   
1  brinquedo   Boneco One Piece Styling Law Luffy Zoro Mihaw...   
2      livro   Box Série Fallen 5 Livros Lauren Kate  Box Sé...   
3       game   Mini Game Portátil 10mil Jogos Player Mp3 Mp4...   
4  maquiagem   Kit Anel Micropigmentação 2 Anéis + 100 Batoq...   

                                       texto_Treated  
0  [apanhador, campo, centeio, produto, novoum, g...  
1  [boneco, one, piece, styling, law, luffy, zoro...  
2  [box, serie, fallen, livros, lauren, kate, box...  
3  [mini, game, portatil, mil, jogos, player, nov...  
4  [kit, anel, micropigmentacao, aneis, batoques,...

Agora vamos criar variáveis que serão os hiperparametros de entrada para a construção do Word2Vec usando o gensim. O gensim é uma biblioteca criada para documentos como um vetor semântico de maneira e menos dolorida possível.

In [12]:
# parâmetros do word2vec
dim_vec = 300 # dimensão
min_count = 10 # palavras que apareçam pelo menos 10x no dicionário
window = 4 # 4 palavras antes e 4 palavras depois
num_workers = multiprocessing.cpu_count() # cpu disponíveis no computador
seed = np.random.seed(42)

Com isso, podemos criar um modelo do Word2Vec a partir dos dados da coluna tratada. Importante notar que esse exemplo não captura tudo aquilo que o Word2Vec pode oferecer, visto que na prática treinamos com uma quantidade muito maior de texto. O objetivo aqui é apenas ilustrar o processo de treinamento de embbedings. Mesmo assim, veremos que os resultados serão muito satisfatórios.

In [13]:
# instância do Word2Vec
modelo = Word2Vec(df['texto_Treated'],
                  min_count = min_count,
                  vector_size = dim_vec,
                  window = window,
                  seed = seed,
                  workers = num_workers,
                  sg = 1) # sg = 0 -> CBOW e sg = 1 -> skipgram

# sg (Skip-gram): Prever as palavras que estão a uma certa distância (contexto) da palavra central (target).
# cbow (continuous bag of word): Reconstruir a palavra central (target) com base em um contexto de palavras ao seu redor

Podemos verificar o tamanho do vocabulário que o modelo criou:

In [14]:
print('Tamanho do vocabulário do Word2Vec: ', len(modelo.wv))

Tamanho do vocabulário do Word2Vec:  4802


Treinado o modelo, conseguimos explorar um pouco as relações semânticas que ele consegue estabelecer. Veja os exemplos a seguir:

In [17]:
# exemplos das relações semânticas que o word2vec consegue estabelecer
print(modelo.wv.most_similar('mario'), '\n') # palavra mais similar a 'mario'
print(modelo.wv.similarity('mario', 'game'), '\n') # similaridade entre duas palavras
print(modelo.wv.most_similar(positive=['mario', 'luigi'], negative = ['game'], topn = 3)) # similaridade considerando exemplos positivos e negativos

[('bros', 0.9634052515029907), ('sayajin', 0.9289910197257996), ('saiyan', 0.9287723302841187), ('luigi', 0.9283984303474426), ('gohan', 0.9069422483444214), ('sonic', 0.906664252281189), ('figuarts', 0.9064435362815857), ('bandai', 0.900736391544342), ('trunks', 0.9004477858543396), ('majin', 0.8980379700660706)] 

0.5753375 

[('trunks', 0.8345196843147278), ('majin', 0.8313191533088684), ('gohan', 0.8286373019218445)]


O Word2Vec treinado retorna um vetor de 300 dimensões para cada palavra. Entretanto, estamos trabalhando com frases. Dessa maneira, precisamos calcular o vetor das frases. Para isso, considere o seguinte código:

In [18]:
# Embedding para ser representado por uma frase

def meanVector(model,phrase):
    vocab = list(model.wv.index_to_key) #Retorna uma lista com as palavras que formam o vocabulário do modelo
    phrase = " ".join(phrase) #Junta as palavras numa string só
    phrase = [x for x in word_tokenize(phrase) if x in vocab] #Mantém na variável apenas palavras que estão no dicionário
    #Quando não houver palavra o vector recebe 0 para todas as posições
    if phrase == []:
        vetor = [0.0]*dim_vec
    else:
        #Caso contrário, calcula um vetor com a média do vetor de cada palavra na frase
        vetor = np.mean([model.wv[word] for word in phrase],axis=0)
    return vetor

Agora, criamos outra função que usará a função criada anteriormente para retornar as features que serão imputadas no modelo a ser treinado:

In [19]:
# Função para retornar as features para inputar no modelo
def createFeatures(base):  #Cria uma função chamada createFeatures que recebe o dataframe como parâmetro
    #Calcula o vetor médio de cada frase presente na base e retorna num formato de lista de listas
    features = [meanVector(modelo,base['texto_Treated'][i])for i in range(len(base))]
    return features

Criaremos uma variável labels, que conterá os rótulos das amostras de treinamento:

In [21]:
labels = np.array(df['categoria']) # label para cada uma das frases

In [22]:
df = createFeatures(df)

In [23]:
df

[array([ 1.95917457e-01,  2.12566420e-01,  6.59103692e-02,  2.60707363e-02,
        -1.80192024e-01,  2.56718621e-02, -5.61738294e-03, -2.86085933e-01,
        -1.58691958e-01, -2.02709824e-01, -2.75103692e-02, -7.30206966e-02,
         1.44923687e-01,  1.24033146e-01,  6.49273023e-02,  1.01225704e-01,
         5.06778024e-02, -1.54123887e-01,  7.41045643e-03,  6.86739981e-02,
        -7.91595653e-02,  9.46309068e-04,  5.18071763e-02, -1.47418275e-01,
         1.13975555e-02, -3.63661200e-02, -5.93309253e-02,  1.06683947e-01,
        -8.14444050e-02, -1.36306152e-01, -7.95956552e-02,  2.48764083e-01,
        -6.87520951e-02,  3.51528861e-02,  2.97990143e-02,  7.79984444e-02,
         1.28641620e-01, -1.42173737e-01,  1.52438372e-01, -5.49010299e-02,
         8.72883871e-02, -1.60108775e-01,  4.52136658e-02,  2.15570450e-01,
         1.88667789e-01,  3.03956978e-02,  1.40611425e-01,  1.25857024e-02,
        -1.14071760e-02,  6.77826703e-02,  8.40236768e-02, -1.67442694e-01,
         4.0

Separamos os dados em conjunto de treino e teste, instanciamos e treinamos um modelo SVM, calculando o tempo de treinamento e fazemos a predição do conjunto de teste:

In [24]:
X_train, X_test, y_train, y_test = train_test_split(df, labels, test_size=0.3, random_state=42)
clf = svm.SVC(kernel='rbf') # utiliza uma função de base radial como kernel
# SVM com kernel RBF é um escolha sólida quando se lida com conjuntos de dados complexos e não lineares
start_time = time.time()
clf.fit(X_train, y_train)
end_time = time.time()
y_pred = clf.predict(X_test)

In [25]:
import datetime
sec = end_time-start_time
print(str(datetime.timedelta(seconds = sec)))

0:00:00.134208


Por fim, imprimimos o valor da acurácia no conjunto de teste:

In [26]:
print('Accuracy:', metrics.accuracy_score(y_test, y_pred))

Accuracy: 0.9874285714285714


In [27]:
# Frases fornecidas
frases = ['A O Reilly separou alguns dos melhores insights de especialistas em matéria de programação e membros da indústria para que programadores possam mergulhar profundamente no mais recente do que está acontecendo no mundo da engenharia de software, arquitetura e código aberto.',
          'A Maybelline NY criou um Testador Virtual que te ajuda a escolher a tonalidade do seu corretivo, usando a câmera do seu smartphone. Nessa plataforma, é usado recurso de Inteligência Artificial que identifica através da sua foto, o tom da sua pele, sendo assim, sugere o tom ideal para você usar.',
          'A saga Zelda é uma série de jogos de ação e aventura desenvolvida pela Nintendo, que começou em 1986 com o lançamento de “The Legend of Zelda” para o console NES. Ela é centrada em torno de Link, um herói corajoso e destemido que luta contra forças do mal para salvar a Princesa Zelda e o Reino de Hyrule',
          'Mario Bro Nintendo']

# Criar um DataFrame
data = {'texto_Treated': frases}
df_novo_teste = pd.DataFrame(data)

df_novo_teste['texto_Treated'] = df_novo_teste['texto_Treated'].apply(tokenizer)

# Criação dos vetores de média para o novo teste
features_novo_teste = createFeatures(df_novo_teste)

# Realiza as previsões com o modelo treinado
y_pred_novo_teste = clf.predict(features_novo_teste)
print(y_pred_novo_teste)

['livro' 'maquiagem' 'game' 'game']
